In [1]:
#Trying to replicate the results of "Adaptive activation functions accelerate convergence in deep and physics-informed neural networks"
import torch
import torch.autograd as autograd         # computation graph
from torch import Tensor                  # tensor node in the computation graph
import torch.nn as nn                     # neural networks
import torch.optim as optim               # optimizers e.g. gradient descent, ADAM, etc.

import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec
from mpl_toolkits.axes_grid1 import make_axes_locatable
from mpl_toolkits.mplot3d import Axes3D
import matplotlib.ticker
from torch.nn.parameter import Parameter

import numpy as np
import time
from pyDOE import lhs         #Latin Hypercube Sampling
import scipy.io
from scipy.io import savemat

from smt.sampling_methods import LHS

#Set default dtype to float32
torch.set_default_dtype(torch.float)

#PyTorch random number generator
torch.manual_seed(1234)

# Random number generators in other libraries
np.random.seed(1234)

# Device configuration
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')

print(device)

if device == 'cuda': 
    print(torch.cuda.get_device_name())


cuda:0


In [2]:
lr_tune = np.array([8e-6,8e-5,8e-4,8e-3,8e-2]).reshape(-1,1)
b_value = np.array([0.0,0.25,0.5,1.0]).reshape(-1,1)


LR_tune, B_value = np.meshgrid(lr_tune,b_value)

LR_tune = LR_tune.flatten('F').reshape(-1,1)
B_value = B_value.flatten('F').reshape(-1,1)


lrb_tune = np.hstack((LR_tune,B_value))

In [3]:
def true_smooth(x): #[-3,3]
    term1 = (np.power(x,3) - x)
    term2 = np.sin(7*x)/7  
    
    term3 = np.sin(12*x)
    term12 = np.multiply(term1,term2)

    return 50*(term12  + term3)

In [4]:
# Domain bounds
label = "Regr_smooth_Stan"
loss_thresh = 0.1

lb = np.array(-3.0)  # [-1. 0.]
ub = np.array(3.0) # [1.  0.99]

x_test = np.linspace(lb,ub,1000).reshape(-1,1)
u_true = true_smooth(x_test)

u_true_norm = np.linalg.norm(u_true,2)

In [5]:
def trainingdata(N_train,seed):
    np.random.seed(seed)
    
    x_train = np.random.uniform(low=lb, high=ub, size=(N_train,)).reshape(-1,1)

    u_train = true_smooth(x_train)

    return x_train, u_train

In [6]:
class Sequentialmodel(nn.Module):
    
    def __init__(self,layers,beta_init):
        super().__init__() #call __init__ from parent class 
              
        'activation function'
        self.activation = nn.Tanh()
     
        'loss function'
        self.loss_function = nn.MSELoss(reduction ='mean')
        
        'Initialise neural network as a list using nn.Modulelist'  
        self.linears = nn.ModuleList([nn.Linear(layers[i], layers[i+1]) for i in range(len(layers)-1)])
     
        
        for i in range(len(layers)-1):
            nn.init.xavier_normal_(self.linears[i].weight.data, gain=1.0)
            # set biases to zero
            nn.init.zeros_(self.linears[i].bias.data)

        
        self.beta = Parameter(beta_init*torch.ones((layers[1],len(layers)-2)))
        self.beta.requiresGrad = True
            
            
    'foward pass'
    def forward(self,x):
        if torch.is_tensor(x) != True:         
            x = torch.from_numpy(x)                
        
        u_b = torch.from_numpy(ub).float().to(device)
        l_b = torch.from_numpy(lb).float().to(device)
                      
        #preprocessing input 
        x = (x - l_b)/(u_b - l_b) #feature scaling
        
        #convert to float
        a = x.float()
        
        for i in range(len(layers)-2):
            z = self.linears[i](a)
            a = self.activation(z) + self.beta[:,i]*z*self.activation(z)
    
        a = self.linears[-1](a) 
        
        return a
    
    
    def loss(self,x,u):

        loss_val = self.loss_function(self.forward(x),u)
        
        return loss_val
        
    'test neural network'
    def test(self):
        u_pred = self.forward(x_test_tensor)       
        u_pred = u_pred.cpu().detach().numpy()
        
        return u_pred
    
    def test_loss(self):
        u_pred = self.test()
        
        test_mse_loss = np.mean(np.square(u_pred.reshape(-1,1) - u_true.reshape(-1,1)))
        test_re_loss = np.linalg.norm(u_pred.reshape(-1,1) - u_true.reshape(-1,1),2)/u_true_norm
        
        return test_mse_loss, test_re_loss  

In [7]:
def data_update(loss_np):
    train_loss.append(loss_np)
    beta_val.append(model_NN.beta.cpu().detach().numpy())
    test_mse, test_re = model_NN.test_loss()
    test_mse_loss.append(test_mse)
    test_re_loss.append(test_re)

In [8]:
def train_step():
    optimizer.zero_grad()     # zeroes the gradient buffers of all parameters
    loss = model_NN.loss(x_train,u_train)
    loss.backward() #backprop
    optimizer.step()
    
    return loss

In [9]:
def train_model(max_iter,rep):
    print(rep) 
   
    torch.manual_seed(rep*123)
    start_time = time.time()
    thresh_flag = 0
    
    nan_flag = 0  
    
    for i in range(max_iter):
        loss_np = train_step().cpu().detach().numpy()
        if(thresh_flag == 0):
            if(loss_np < loss_thresh):
                time_threshold[rep] = time.time() - start_time
                epoch_threshold[rep] = i+1            
                thresh_flag = 1
                
        data_update(loss_np)
        print(i,"Train Loss",train_loss[-1],"Test MSE",test_mse_loss[-1],"Test RE",test_re_loss[-1])
        if(np.isnan(loss_np)):
            nan_flag =1
            print("NAN BREAK!")
            break
    
    elapsed_time[rep] = time.time() - start_time
    print('Training time: %.2f' % (elapsed_time[rep]))
    
    return nan_flag

In [10]:
nan_tune = []

for tune_reps in range(25):
    label = "Regr_stan_tune"+str(tune_reps) 

    max_reps = 10
    max_iter = 500
    layers = np.array([1,50,50,50,50,1])

    train_loss_full = []
    test_mse_full = []
    test_re_full = []
    beta_full = []
    elapsed_time= np.zeros((max_reps,1))

    time_threshold = np.empty((max_reps,1))
    time_threshold[:] = np.nan
    epoch_threshold = max_iter*np.ones((max_reps,1))
    
    beta_init = lrb_tune[tune_reps,1]
    
    for reps in range(max_reps):

        train_loss = []
        test_mse_loss = []
        test_re_loss = []
        beta_val = []
        'Generate Training data'
        N_train = 300

        x_train_np_array, u_train_np_array = trainingdata(N_train,reps*1234)

        'Convert to tensor and send to GPU'
        x_train = torch.from_numpy(x_train_np_array).float().to(device)
        u_train = torch.from_numpy(u_train_np_array).float().to(device)

        x_test_tensor = torch.from_numpy(x_test).float().to(device)


        model_NN = Sequentialmodel(layers,beta_init)
        model_NN.to(device)
        print(model_NN)
        params = list(model_NN.parameters())
        #optimizer = optim.Adam(PINN.parameters(), lr=0.0008,betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
        optimizer = optim.Adam(model_NN.parameters(), lr=lrb_tune[tune_reps,0])

        nan_flag = train_model(max_iter,reps)

        torch.save(model_NN.state_dict(),label+'_'+str(reps)+'.pt')
        train_loss_full.append(train_loss)
        test_mse_full.append(test_mse_loss)
        test_re_full.append(test_re_loss)
        beta_full.append(beta_val)
        
        if(nan_flag == 1):
            nan_tune.append(tune_reps)
            break


    mdic = {"train_loss": train_loss_full,"test_mse": test_mse_full, "test_re": test_re_full,"Time": elapsed_time, "Thresh_time": time_threshold, "epoch_thresh": epoch_threshold,"beta": beta_full, "label": label}
    savemat(label+'.mat', mdic) 

Sequentialmodel(
  (activation): Tanh()
  (loss_function): MSELoss()
  (linears): ModuleList(
    (0): Linear(in_features=1, out_features=50, bias=True)
    (1): Linear(in_features=50, out_features=50, bias=True)
    (2): Linear(in_features=50, out_features=50, bias=True)
    (3): Linear(in_features=50, out_features=50, bias=True)
    (4): Linear(in_features=50, out_features=1, bias=True)
  )
)
0
0 Train Loss 3616.8254 Test MSE 3506.5301928331014 Test RE 0.9998632386318451
1 Train Loss 3616.8052 Test MSE 3506.5204993264824 Test RE 0.9998618566121437
2 Train Loss 3616.7852 Test MSE 3506.510805847828 Test RE 0.9998604745945191
3 Train Loss 3616.7651 Test MSE 3506.5011126286704 Test RE 0.9998590926119812
4 Train Loss 3616.7446 Test MSE 3506.491419168771 Test RE 0.99985771059321
5 Train Loss 3616.7246 Test MSE 3506.4817255854214 Test RE 0.9998563285549279
6 Train Loss 3616.7043 Test MSE 3506.4720318487957 Test RE 0.9998549464928825
7 Train Loss 3616.6843 Test MSE 3506.462337991551 Test RE 

100 Train Loss 3614.7893 Test MSE 3505.5563059313504 Test RE 0.9997243803761183
101 Train Loss 3614.7683 Test MSE 3505.5464779982663 Test RE 0.9997229789963741
102 Train Loss 3614.748 Test MSE 3505.536647798269 Test RE 0.9997215772914222
103 Train Loss 3614.727 Test MSE 3505.526814998067 Test RE 0.9997201752137366
104 Train Loss 3614.7068 Test MSE 3505.5169801370894 Test RE 0.9997187728402339
105 Train Loss 3614.686 Test MSE 3505.5071422881747 Test RE 0.999717370038707
106 Train Loss 3614.6655 Test MSE 3505.4973021581513 Test RE 0.9997159669099425
107 Train Loss 3614.6443 Test MSE 3505.4874593875948 Test RE 0.9997145634026877
108 Train Loss 3614.6238 Test MSE 3505.477614145966 Test RE 0.9997131595411046
109 Train Loss 3614.603 Test MSE 3505.4677662639833 Test RE 0.9997117553010538
110 Train Loss 3614.5825 Test MSE 3505.457915738495 Test RE 0.9997103506820841
111 Train Loss 3614.5618 Test MSE 3505.4480625017763 Test RE 0.9997089456745367
112 Train Loss 3614.541 Test MSE 3505.43820647707

204 Train Loss 3612.596 Test MSE 3504.5177808792196 Test RE 0.9995762846632155
205 Train Loss 3612.5742 Test MSE 3504.507606523086 Test RE 0.9995748336715068
206 Train Loss 3612.5525 Test MSE 3504.497428032429 Test RE 0.9995733820880558
207 Train Loss 3612.5312 Test MSE 3504.4872455796617 Test RE 0.9995719299374475
208 Train Loss 3612.5098 Test MSE 3504.4770587005237 Test RE 0.9995704771534698
209 Train Loss 3612.4875 Test MSE 3504.466867799521 Test RE 0.9995690237938082
210 Train Loss 3612.4663 Test MSE 3504.4566733774473 Test RE 0.9995675699298806
211 Train Loss 3612.4446 Test MSE 3504.44647429683 Test RE 0.9995661153994644
212 Train Loss 3612.4233 Test MSE 3504.4362712204597 Test RE 0.9995646602970811
213 Train Loss 3612.4014 Test MSE 3504.426063945829 Test RE 0.9995632045938467
214 Train Loss 3612.3796 Test MSE 3504.415852713949 Test RE 0.9995617483241311
215 Train Loss 3612.358 Test MSE 3504.4056370384797 Test RE 0.999560291418572
216 Train Loss 3612.336 Test MSE 3504.395417204236

309 Train Loss 3610.263 Test MSE 3503.4247256664157 Test RE 0.9994203891385358
310 Train Loss 3610.24 Test MSE 3503.414051580782 Test RE 0.9994188666415821
311 Train Loss 3610.2173 Test MSE 3503.4033724059786 Test RE 0.9994173434164147
312 Train Loss 3610.1943 Test MSE 3503.3926871263034 Test RE 0.9994158193181545
313 Train Loss 3610.171 Test MSE 3503.3819966433466 Test RE 0.9994142944753965
314 Train Loss 3610.1484 Test MSE 3503.3713011841355 Test RE 0.9994127689205198
315 Train Loss 3610.125 Test MSE 3503.3605996261813 Test RE 0.9994112424934136
316 Train Loss 3610.102 Test MSE 3503.349892961496 Test RE 0.999409715335571
317 Train Loss 3610.0793 Test MSE 3503.3391813928297 Test RE 0.9994081874759079
318 Train Loss 3610.056 Test MSE 3503.3284635406267 Test RE 0.9994066587176459
319 Train Loss 3610.033 Test MSE 3503.317740733111 Test RE 0.9994051292502346
320 Train Loss 3610.01 Test MSE 3503.3070117677935 Test RE 0.9994035989021512
321 Train Loss 3609.9868 Test MSE 3503.296277980254 Te

414 Train Loss 3607.7747 Test MSE 3502.272996885105 Test RE 0.9992560990604662
415 Train Loss 3607.75 Test MSE 3502.261720071729 Test RE 0.9992544903289902
416 Train Loss 3607.7256 Test MSE 3502.250437102845 Test RE 0.9992528807167876
417 Train Loss 3607.701 Test MSE 3502.2391479053554 Test RE 0.9992512702134261
418 Train Loss 3607.6763 Test MSE 3502.227853550414 Test RE 0.9992496589717115
419 Train Loss 3607.6519 Test MSE 3502.2165533879847 Test RE 0.999248046898906
420 Train Loss 3607.6277 Test MSE 3502.2052472489413 Test RE 0.9992464339708784
421 Train Loss 3607.6025 Test MSE 3502.19393538944 Test RE 0.9992448202241678
422 Train Loss 3607.5781 Test MSE 3502.1826178595047 Test RE 0.9992432056659065
423 Train Loss 3607.5535 Test MSE 3502.171294194384 Test RE 0.9992415902297891
424 Train Loss 3607.5283 Test MSE 3502.159964778376 Test RE 0.9992399739706354
425 Train Loss 3607.504 Test MSE 3502.1486301560635 Test RE 0.9992383569661321
426 Train Loss 3607.4792 Test MSE 3502.1372893967173 

...

149 Train Loss 3197.3623 Test MSE 3755.9679909009506 Test RE 1.0348150852141256
150 Train Loss 3701.4048 Test MSE 4294.942252662771 Test RE 1.106574031834579
151 Train Loss 4113.681 Test MSE 3928.7240424450915 Test RE 1.0583457549297477
152 Train Loss 3958.6467 Test MSE 2778.3845981199443 Test RE 0.8900163630571736
153 Train Loss 2748.3718 Test MSE 3923.660115005091 Test RE 1.0576634578073134
154 Train Loss 3810.1343 Test MSE 3091.203332433396 Test RE 0.9387838209318327
155 Train Loss 2992.8887 Test MSE 3303.4408334589666 Test RE 0.970476617968025
156 Train Loss 3280.718 Test MSE 3413.6749736754837 Test RE 0.9865359003674765
157 Train Loss 3394.8743 Test MSE 3501.718690453413 Test RE 0.9991770195596511
158 Train Loss 3497.2275 Test MSE 3348.635833800617 Test RE 0.9770927031634294
159 Train Loss 3336.53 Test MSE 3225.9329859547997 Test RE 0.9590240106132679
160 Train Loss 3187.3237 Test MSE 3092.385258639871 Test RE 0.9389632764770346
161 Train Loss 3008.1428 Test MSE 3172.316315334559 

255 Train Loss 3119.3088 Test MSE 3239.0209779319625 Test RE 0.9609674783542062
256 Train Loss 3191.6106 Test MSE 3808.852434652806 Test RE 1.0420747755196633
257 Train Loss 3589.0117 Test MSE 3318.828839895725 Test RE 0.9727343169302507
258 Train Loss 3335.6484 Test MSE 3255.781520648441 Test RE 0.9634505672984381
259 Train Loss 3248.87 Test MSE 3541.32557705917 Test RE 1.004811826291696
260 Train Loss 3391.722 Test MSE 3149.4339264085247 Test RE 0.9475847453022881
261 Train Loss 3060.8933 Test MSE 3174.555341929606 Test RE 0.9513564372412101
262 Train Loss 3162.4993 Test MSE 3120.116651147749 Test RE 0.9431640213302652
263 Train Loss 3100.933 Test MSE 3251.880995041185 Test RE 0.962873272753531
264 Train Loss 3125.0293 Test MSE 3022.010399388453 Test RE 0.9282175749324548
265 Train Loss 3002.5637 Test MSE 2949.1448651122146 Test RE 0.9169588847579654
266 Train Loss 2904.5608 Test MSE 2991.855716577759 Test RE 0.9235749236546249
267 Train Loss 2885.2642 Test MSE 3023.0762506494307 Tes

359 Train Loss 3417.2285 Test MSE 3458.838194805154 Test RE 0.9930404356719442
360 Train Loss 3402.767 Test MSE 3475.4851935004126 Test RE 0.9954272631262862
361 Train Loss 3404.1348 Test MSE 3459.5564819406723 Test RE 0.9931435412672384
362 Train Loss 3392.4795 Test MSE 3435.0383004099567 Test RE 0.9896180358886946
363 Train Loss 3387.585 Test MSE 3424.8000241758173 Test RE 0.9881421362183885
364 Train Loss 3384.308 Test MSE 3424.400786680883 Test RE 0.9880845394410509
365 Train Loss 3368.4282 Test MSE 3439.076727455087 Test RE 0.9901995907292247
366 Train Loss 3367.7659 Test MSE 3410.8658458513205 Test RE 0.9861299045077168
367 Train Loss 3348.2732 Test MSE 3391.4844086407807 Test RE 0.9833241883302011
368 Train Loss 3342.35 Test MSE 3382.410520851956 Test RE 0.9820078695249799
369 Train Loss 3323.113 Test MSE 3388.021647740064 Test RE 0.9828220651106827
370 Train Loss 3309.4263 Test MSE 3364.91006596775 Test RE 0.979464140521168
371 Train Loss 3292.981 Test MSE 3342.4128486080076 Te

464 Train Loss 12519.052 Test MSE 153041.1665553003 Test RE 6.605503752089629
465 Train Loss 152596.38 Test MSE 3364758.144976947 Test RE 30.972676494837618
466 Train Loss 3400731.5 Test MSE 4587.05165659623 Test RE 1.1435854610529008
467 Train Loss 4705.885 Test MSE 3673.5981962207866 Test RE 1.0234052403237526
468 Train Loss 3565.3762 Test MSE 29110.118962018856 Test RE 2.880870921486917
469 Train Loss 28894.555 Test MSE 3873.3543098156956 Test RE 1.050861357880045
470 Train Loss 3997.0505 Test MSE 19098.374223038325 Test RE 2.3334581122651556
471 Train Loss 18315.074 Test MSE 3893856.964393898 Test RE 33.318988377179956
472 Train Loss 3946631.0 Test MSE 4432061.480230407 Test RE 35.547142726582294
473 Train Loss 4451861.5 Test MSE 3134534.518453134 Test RE 29.894296541298978
474 Train Loss 3163542.0 Test MSE 136123.71495604707 Test RE 6.229722567150207
475 Train Loss 139247.39 Test MSE 209011.2307210857 Test RE 7.719454666971074
476 Train Loss 212667.66 Test MSE 107939.38996182966 T

IndexError: index 20 is out of bounds for axis 0 with size 20

In [ ]:
u_pred = model_NN.test()

In [ ]:
plt.plot(x_test,u_pred,'rx')
plt.plot(x_test,u_true,'b')

In [12]:
import scipy.io as sio
import numpy as np

for tune_reps in range(20):
    label = "Regr_stan_tune"+str(tune_reps)+".mat"
    data = sio.loadmat(label)
    re = np.array(data["test_re"])
    print(tune_reps," ",np.mean(re[:,-1]))

0   0.9994425333629676
1   0.9994390248414355
2   0.9994396438961639
3   0.9994036073086685
4   0.9978498015810631
5   0.997684158430661
6   0.9976175571373818
7   0.9954119897674861
8   0.7844356453603767
9   0.6562893381505053
10   0.5559536311076493
11   0.4890577702983553
12   0.5190091032377804
13   0.5306830703304191
14   0.49264660095676416
15   0.4580122687163282
16   1.0900105767250567
17   6.805519715507998
18   31.39129029560872
19   1.1803850482835254


In [13]:
lrb_tune[15]

array([0.008, 1.   ])